# Networking

## Linux networking

- Overview of network protocols and TCP/IP in Linux.
- Network configuration in Linux.
- Netplan on Ubuntu servers.
- Network settings in Red Hat.
- Network applications and services.
- Network calculation with <TT>ipcalc</TT>
<hr>

## Computers on the intertnet

- Network communication allows sending information, transfering files, and managing applications remotely between computers.
- Networks are organized in a series of layers implemented on each machine.
- The layers are independent and each layer offers a specific task to the neighboring layers above and below.
- The communication between the layers is based on defined rules and procedures, called protocols.
- Data is processed and passed through the layers from above to below, until the bottom layer is reached.
- At the bottom layer, computers communicate with each other via sending and receiving network datagrams through - cables, switches and routers.

<hr>

## TCP/IP 5 layer protocol suit


![](img/tcp-ip.jpg)

Each layer has its own task:


|TCP/IP Protocol Layer | Tasks
| :-- | :--
|5. Application Layer: ssh, ftp, http ... | Data segmentation by the application into Message Transfer Unit (MTU) segments. Typical MTU is 1.5 Kbyte
|4. Transport Layer: TCP, UDP, ports  | Connection management, quality, and ports to the applications
|3. Internet Layer: IP addresses, subnets, routing | Addressing: each computer has a unique address on its network or subnet. Routing between networks.
|2. Link Layer: Ethernet | Communication on the local network (subnet) through a switch. Media Access Card (MAC) address unique on the subnet. For example, 48:d2:4f:f4:d:fb, should be unique within a subnet. Address Resolution Protocol (ARP) matches the IP address to MAC on the subnet.
|1. Physical Layer: NIC, hubs, switches, routers, cabling, wifi APs and cards | Electronic devices to send and receive signals between computers.

<hr>

## OSI 7 layer Network Stack Model

![](img/osi.jpg)

|TCP/IP Protocol Layer | Task
| :-- | :--
|7. Application Layer: ssh, ftp, http ... | Data segmentation by the application into Message Transfer Unit (MTU) segments. Typical MTU is 1.5 Kbyte
|6. Presentation Layer: SSL, libz, XDR  | Data encryption, compression, and encoding/decoding
|5. Session Layer: Remote Procedure Call (RPC) | Responsible for opening, using and closing sessions. Remote procedures.

<hr>

## TCP/IP and Kernel

![](img/tcpip-kernel.jpg)

The Link, Internet and Transport layers are implemented through kernel.

<hr>

## Packet Encapsulation

Data is processed in form of packet encapsulation and transmitted/received in form of Ethernet frames.

![](img/ip_packet.jpg)

<hr>

## Hosts communication via TCP/IP

![](img/host-host.jpg)

![](img/host-tcpip.jpg)

<hr>

## Wired connection checkup (Exercise)

- To see whether your desktop is connected to a network switch and at what speed, use command  ```ethtool```.

- On your desktop, install package <TT>ethtool</TT>:
```bash
apt install ethtool
```
- See your network interfaces with command ```ifconfig``` or ```ip a```:
```bash
ifconfig -a
```
or 
```bash
ip a
```

The main network interface, connected to the Ethernet, is <TT>eno1</TT>. Run command below:
```bash
ethtool eno1
```
In the output, among various parameters, it shows 
  - Speed: 1000Mb/s, 
  - Duplex: Full, 
  - Link detected: yes
  
Which means the cable is connected and the link speed is 1Gb/s speed, full duplex mode. 
  <hr>

## Network IP configuration

- Static configuration
    - IP address, gateway, and Dynamic Name Service (DNS) are configured on the host.
    
    
    
- Dynamic Host Configuration Protocol (DHCP)
    - The settings are obtained from a DHCP server.
    
![](img/dhcp.gif)

<hr>

## Environment for IP configuration on Ubuntu and RedHat

|ifupdown scripts	| Network Manager service 	| Netplan networkd service Meaning
|:---    | ---      | ---:        |  
|Old Debian/Ubuntu: | Ubuntu desktop, Debian: | Ubuntu server: |
|File: ```/etc/network/interfaces``` |  Commands: ```nmtui, nmcli```     | File:```/etc/netplan/01-netcfg.yaml ``` |
|RedHat:                 | RedHat:                   | Command: ```netplan apply``` |
|File: ```/etc/sysconfig/network-scripts/ifcfg-eth0```| File: ```/etc/sysconfig/network-scripts/ifcfg-eth0```  |
|Command:```ifup eth0```  | Command: ```ifup eth0``` 




<HR>



## Deploy a new VM for exercises

Shutdown <TT>kvm1</TT> VM, and clone it into <TT>netplan</TT> VM:
```bash
virsh shutdown kvm1
virt-clone  -o kvm1 -n netplan -f /home/hostadm/KVM/netplan.qcow2
```
Start netplan. Login to console of netplan:
```bash
virsh console netplan
```
Fix the hostname in file <TT>/etc/hostname</TT>.
Reset the machine ID by running the following commands on netplan:
```bash
rm -f /etc/machine-id
rm /var/lib/dbus/machine-id
dbus-uuidgen --ensure=/etc/machine-id
dbus-uuidgen --ensure
```
Clear the DHCP leased IP settings:
```bash
dhclient -r ens3
```
Execute command reboot on netplan:
```bash
reboot
```

<hr>


## Configuring network settings on Ubuntu server with Netplan (Exercises)

On <TT>netplan</TT> VM check the IP address settings by running command below:
```bash
ip addr
```

Assign IP address <TT>192.168.122.222</TT> by modifying the content of ```/etc/netplan/01-netcfg.yaml``` as follows:
<hr>
<pre>
network: 
  version: 2
  renderer: networkd
  ethernets:
   ens3:
     dhcp4: no
     addresses: [192.168.122.222/24]
     gateway4: 192.168.122.1
     nameservers:
       addresses: [192.168.122.1]
   </pre> 
<hr>

Have the settings applied:
```bash
netplan apply
```
Check the IP address again:
```bash
ip addr
```
It should show <TT>192.168.122.222</TT> for <TT>ens3</TT> interface now.

See the gateway settings by running command 
```bash
ip route show
```
It should show the "default via 192.168.122.1"
<hr>

## Network configurations on a Red Hat server (Exercises)
Start CentOS7 VMs:
```bash
virsh start CentOS7
```
Login to console of CentOS7:
```bash
virsh console CentOS7
```
Execute command ip address show to read the IP address:
```bash
ip addr show eth0
```
Try pinging netplan by its IP address, for example:
```bash
ping -c 3 192.168.122.222
```
Become root on CentOS7 VM
```bash
sudo -s
```
Reconfigure eth0 network interface on CentOS7:
```bash
ifconfig eth0 192.168.122.126 netmask 255.255.255.0 up
```
Verify the network settings:
```bash
ifconfig eth0
```
Ping netplan by the IP address:
```bash
ping -c 3 192.168.122.222
```
Reset the network setting to the default on CentOS7 VMs:
```bash
ifdown eth0
ifup eth0
```
Check the updated network settings on the VM:
```bash
ifconfig eth0
```
Static IP configuration on CentOS7 VMs.
On CentOS7, edit file ```/etc/sysconfig/network-scripts/ifcfg-eth0``` and put the following settings for the static IP configuration there:
<pre>
DEVICE=eth0
TYPE=Ethernet
ONBOOT=yes
BOOTPROTO=none
IPADDR=192.168.122.126
NETMASK=255.255.255.0
NETWORK=192.168.122.0
BROADCAST=192.168.122.255
</pre>
Apply the network settings:
```bash
ifdown eth0
ifup eth0
```
Ping netplan by the IP address:
```bash
ping -c 3 192.168.122.222
```
Restore the interface settings to DHCP on CentOS7 VMs.
On CentOS7, edit file ```/etc/sysconfig/network-scripts/ifcfg-eth0``` and put the following settings for DHCP configuration:
<pre>
NETWORKING=yes 
DEVICE=eth0 
TYPE=Ethernet 
ONBOOT=yes 
BOOTPROTO=dhcp
</pre>
Reset the network settings:
```bash
ifdown eth0
ifup eth0
```
Verify the network settings:
```bash
ifconfig eth0
```
The interface should acquire some IP address on <TT>192.168.122.0</TT> network.

<hr>

## Internet Control Message Protocol (ICMP) protocol (Exercises)

Implemented on hosts and gateways (routers) for:

Reporting the status of datagram processing.
Diagnostics of connection and routing.
Reporting errors in the processing of a datagram.

Example: ```ping```

![](img/ping.jpg)

Exercise: command ```ping```.
```bash
ping -c 5 capone
ping -c 5 engsoft.rutgers.edu
ping -c 5 google.com
```
If the systems respond, it means they are reachable on the network. Notice how varies the round-trip time and Time to Live (ttl) for packets between the hosts.

Example: ```traceroute```

![](img/traceroute.jpg)

Time to leave (TTL) decrement. The TTL value of an IP packet represents the maximum number of IP routers that the packet can go through before being thrown away. You can expect each router in the Internet to decrement the TTL field by exactly one. The default TTL for traceroute on Linux is 30. It can be increased up to 255 maximum by using the -m command option.

Exercise: command traceroute.
```bash
sudo /usr/sbin/traceroute -I capone
sudo /usr/sbin/traceroute -I engsoft.rutgers.edu
sudo /usr/sbin/traceroute -I google.com
```
This shows you all the gateways between the subnets your packet travels towards the destination. Notice the difference in the number of gateways between your desktop and the three remote hosts as well as the round trip times.

<hr>

## Network services (Exercises)

Make sure virtual machine netplan is running
```bash
virsh list
```
Figure out the IP address of netplan:
```bash
virsh domifaddr netplan
```

Place the IP address and netplan host name into file ```/etc/hosts``` on your desktop. 
netplan  IP is 192.168.122.222
```bash
nano /etc/hosts
```
Make entry in the file:  ```192.168.122.222   netplan```

ssh to netplan as user hostadm:
```bash
ssh hostadm@netplan
```

Configure SSH for private/public key authentication.
For SSH authentication, you can use either RSA or DSA public/private keys besides password. We'll be using RSA in the exercises below.
To generate an RSA key pair, type the following command at a shell prompt on your desktop:
```bash
ssh-keygen -t rsa
```
Accept the default file location of ```~/.ssh/id_rsa```. Enter a passphrase different from your account password and confirm it by entering it again.
The public key is written to ```~/.ssh/id_rsa.pub```. The private key is written to ```~/.ssh/id_rsa```.
Never distribute your private key to anyone.
The contents of ```~/.ssh/id_rsa.pub``` needs to be delivered onto the remote machine to which you want to connect, specifically netplan, into file ```~/.ssh/authorized_keys```
To accomplish the transfer task, here you can use sftp service that comes with ssh.
```bash
sftp  netplan
Name (netplan:hostadm): hostadm
sftp> cd .ssh
sftp> lcd .ssh
sftp> put id_rsa.pub authorized_keys
sftp>  quit
```
Command ```cd``` in the sftp> shell above is for stepping into the directory, .ssh, on the remote host, netplan.
Command ```lcd``` is for stepping into the directory, .ssh, on the local desktop.

Now try to ssh to netplan. You should be prompted to enter your passphrase.

The ```ssh-agent``` can be used to store your passphrase so that you do not have to enter it each time you make a ssh or scp connection.
At a shell prompt on the desktop, type the following command:
```bash
exec /usr/bin/ssh-agent $SHELL
```
Then type the command:
```bash
ssh-add
```
and enter your passphrase(s). If you have more than one key pair configured, you will be prompted for each one. When you log out, your passphrase(s) will be forgotten. You must execute these two commands each time you log in to a virtual console or open a terminal window.

Run a remote command over ssh, for example:
```bash
ssh netplan "uname -a"
```
Copy files from your desktop to netplan and vise versa using scp command:
```bash
scp netplan:/etc/hosts .
touch somef.txt
scp somef.txt netplan:/home/$USER
```

Syncronizing directories between remote hosts by using ```rsync```.
This tool lets you copy files and directories between a local host and a remote host.
Install ```rsync``` on both your desktop and netplan:
```bash
apt-get install rsync
```
Creat a directory tree and copy it over to netplan with rsync command.
```bash
mkdir -p dir1/dir2/dir3
rsync  -avz dir1 netplan:/home/$USER
```
Option a stands for archive (preserve links and timestamps); <TT>v</TT> is for verbose and <TT>z</TT> is for data compression when sending-receiving.

<hr>

## Send/receive data with netcat (Exercises)

Netcat is a very useful tool to connect to any TCP and UDP port on a remote host, and send/receive data.


Start both, netplan and CentOS7 VMs:
```bash
virsh start netplan
virsh start CentOS7
```
Login to console of netplan:
```bash
virsh console netplan
```
Bring up another command prompt on the desktop and login to CentOS7
```bash
virsh console CentOS7
```
On each VM, execute command ip addr show to read the IP address:
```bash
ip addr show eth0
```
Become root on both the VMs
```bash
sudo -s
```

| Step | On Ubuntu (server) | On CentOS7 |
|:- | :-: | -: |     
|1.  |Install netcat: ```apt-get install netcat``` | ```yum install nmap-ncat``` | 
|2.    | Start netcat as a server, listening on port UDP/8080: |  Connect to UDP/8080 port on netplan, 192.168.122.222: |  
|      | ```netcat -l -u 8080``` | ```ncat 192.168.122.222 -u 8080``` | 
|3.    | When the session is over, type Ctrl-C to stop the netcat server.  |     Start typing text. Hit ENTER key. The text should appear on the both terminals. Press Ctrl+D to close the UDP connection. | 
|4.    | Start the server on TCP/8080 to write into a file, outputfile.txt |   Send file /etc/hosts to TCP/8080 on netplan VM via netcat |
|   | ```netcat -l 8080 > outputfile.txt```  |  ```ncat 192.168.122.222  8080 < /etc/hosts``` | 
|5.  |  After the file is received, the connection closes itself. Check the content of the file: |  |
|    | ```less outputfile.txt```  |  

 

<hr>

## Subnets and routing

Example: Host A can communicate with both the hosts - B and C. Hosts B and C can't communicate with each other.
What is the problem?
<br>
Answer: the routing (gateway) is not defined on Host B.

![](img/hosts-router.png)

## Network calculation, gateway and routing

- Computers connected to the same switch are on the same network/subnet and communicate with each other directly through the switch.
- For computers located on the different networks/subnets, gateway/router is needed.
- To define the local subnet, netmask is used.

- Subnet mask defines the network and the host parts of the IP address

Network address = Host address (logical AND) Netmask:



| Address         | Decimal/Hexadecimal  | Binary | 
|:- | :-: | :- |                                  
| IP address      | 192.168.5.10  |  11000000 10010100 00000101 00001010 |  
| Netmask         | 255.255.255.0 |  11111111 11111111 11111111 00000000 |
| Network address | 192.168.5.0   |  11000000 10010100 00000101 00000000 |



- The network address is the smallest address on the network:

```11000000 10010100 00000101 00000000 = 192.168.5.0```

- The broadcast address is the largest address on the network:

```11000000 10010100 00000101 11111111 = 192.168.5.255```

- Max number of hosts on the subnet: 254 = 256 - 2
The gateway address should be on the same subnet with the host

<hr>


## IP calculator exercises

Network IP calculations with ipcalc
On the desktop, install ipcalc by using APT:
```bash
apt-get install ipcalc
```
Run ipcalc for network address 192.168.5.0 with subnet mask 255.255.255.0.
```bash
ipcalc 192.168.5.0/255.255.255.0
```
See the output for Address, Netmask, Network, HostMin, HostMax, Broadcast, Hosts/Net.
Notice the same results for the same network and the different representation of the netmask:
```bash
ipcalc 192.168.5.0/24
ipcalc 192.168.5.0/11111111.11111111.11111111.00000000
```
Notice the same results for Netmask, Network, HostMin, HostMax, Broadcast, Hosts/Net if using the different IP addresses within the same network in ipcalc, for example:
```bash
ipcalc 192.168.5.15/24
ipcalc 192.168.5.34/24
```
Run ipcalc for subnets (networks) 192.168.5.0/25 and 192.168.5.128/25:
```bash
ipcalc 192.168.5.0/25
ipcalc 192.168.5.128/25
```
Notice the values for HostMin and HostMax in both the cases. By looking at the ranges [HostMin, HostMax], you can see, for example, that IP address 192.168.5.5 belongs to the first subnet and 192.168.5.250 to the second.
You can verify that by running ipcalc on the IP addresses above and then comparing the Network values:
```bash
ipcalc 192.168.5.5/25
ipcalc 192.168.5.250/25
```

<hr>